In [1]:
# Regular Python library imports 
import xarray as xr 
import numpy as np
import pandas as pd
import pyproj
import scipy.interpolate
import matplotlib.pyplot as plt
import glob
from datetime import datetime
import cartopy.crs as ccrs
import cartopy.feature as cfeature
import os

# Helper functions for reading the data from the bucket and plotting
from utils.read_data_utils import read_IS2SITMOGR4, read_book_data
from utils.plotting_utils import static_winter_comparison_lineplot, staticArcticMaps, interactiveArcticMaps, compute_gridcell_winter_means, interactive_winter_comparison_lineplot # Plotting utils 
from extra_funcs import read_IS2SITMOGR4S, regrid_ubris_to_is2, get_cs2is2_snow, apply_interpolation_time
# Plotting dependencies
#%config InlineBackend.figure_format = 'retina'
import matplotlib as mpl

# Remove warnings to improve display
import warnings 
warnings.filterwarnings('ignore') 

# Get the current working directory
current_directory = os.getcwd()

In [2]:
# Load the winter IS-2 thickness data from zarr/s3
IS2SITMOGR4_v3 = read_IS2SITMOGR4(data_type='zarr-s3', persist=True) 
#IS2SITMOGR4_v3

load zarr from S3 bucket
zarr_path: s3://icesat-2-sea-ice-us-west-2/IS2SITMOGR4_V3/IS2SITMOGR4_V3_201811-202404.zarr


In [3]:
# Get some IS2 map projection/domain info needed for later functions
out_proj = 'EPSG:3411'
mapProj = pyproj.Proj("+init=" + out_proj)

xIS2 = IS2SITMOGR4_v3.x.values
yIS2 = IS2SITMOGR4_v3.y.values
xptsIS2, yptsIS2 = np.meshgrid(xIS2, yIS2)
out_lons = IS2SITMOGR4_v3.longitude.values
out_lats = IS2SITMOGR4_v3.latitude.values

In [4]:
IS2SITMOGR4_v3 = apply_interpolation_time(IS2SITMOGR4_v3, xptsIS2, yptsIS2, ['snow_depth_sm', 'ice_thickness_sm'])

Creating/forcing new variable snow_depth_sm_int
snow_depth_sm 0
Interpolated.
snow_depth_sm 1
Interpolated.
snow_depth_sm 2
Interpolated.
snow_depth_sm 3
Interpolated.
snow_depth_sm 4
Interpolated.
snow_depth_sm 5
Interpolated.
snow_depth_sm 6
Interpolated.
snow_depth_sm 7
Interpolated.
snow_depth_sm 8
Interpolated.
snow_depth_sm 9
Interpolated.
snow_depth_sm 10
Interpolated.
snow_depth_sm 11
Interpolated.
snow_depth_sm 12
Interpolated.
snow_depth_sm 13
Interpolated.
snow_depth_sm 14
Interpolated.
snow_depth_sm 15
Interpolated.
snow_depth_sm 16
Interpolated.
snow_depth_sm 17
Interpolated.
snow_depth_sm 18
Interpolated.
snow_depth_sm 19
Interpolated.
snow_depth_sm 20
Interpolated.
snow_depth_sm 21
Interpolated.
snow_depth_sm 22
no data or issue with gridding, so skipping...
snow_depth_sm 23
no data or issue with gridding, so skipping...
snow_depth_sm 24
no data or issue with gridding, so skipping...
snow_depth_sm 25
no data or issue with gridding, so skipping...
snow_depth_sm 26
no data

In [5]:
# Read in the new summer IS-2 thickness data locally (not on s3 yet)
IS2SITMOGR4_summer_v0 = read_IS2SITMOGR4S(local_data_path="./data/IS2SITMOGR4_SUMMER/")


./data/IS2SITMOGR4_SUMMER/V0/*.nc


In [6]:
# Quick check it looks interpolated..!
# IS2SITMOGR4_v3.ice_thickness_sm_int.isel(time=0).plot()

In [7]:
# Merge winter and summer IS-2 thickness data into one dataset
IS2SITMOGR4_allseason = IS2SITMOGR4_summer_v0.merge(IS2SITMOGR4_v3)

In [8]:
interp_vars=[
 'snow_density',
 'snow_density_sm',
 'snow_depth_mw99',
 'snow_density_w99',
 'ice_thickness_mw99',
 'ice_density_j22',
 'ice_thickness_j22']

IS2SITMOGR4_allseason = apply_interpolation_time(IS2SITMOGR4_allseason, xptsIS2, yptsIS2, interp_vars)

Creating/forcing new variable snow_density_int
snow_density 0
Interpolated.
snow_density 1
Interpolated.
snow_density 2
Interpolated.
snow_density 3
Interpolated.
snow_density 4
Interpolated.
snow_density 5
Interpolated.
snow_density 6
no data or issue with gridding, so skipping...
snow_density 7
no data or issue with gridding, so skipping...
snow_density 8
no data or issue with gridding, so skipping...
snow_density 9
Interpolated.
snow_density 10
Interpolated.
snow_density 11
Interpolated.
snow_density 12
Interpolated.
snow_density 13
Interpolated.
snow_density 14
Interpolated.
snow_density 15
Interpolated.
snow_density 16
Interpolated.
snow_density 17
no data or issue with gridding, so skipping...
snow_density 18
no data or issue with gridding, so skipping...
snow_density 19
no data or issue with gridding, so skipping...
snow_density 20
no data or issue with gridding, so skipping...
snow_density 21
Interpolated.
snow_density 22
Interpolated.
snow_density 23
Interpolated.
snow_density

In [9]:
# Get UBRIS/UIT CS-2 data
start_date_cs2 = "Oct 2018"
end_date_cs2 = "July 2021"
# NB: MS indicates a time frequency of start of the month
date_range_cs2 = pd.date_range(start=start_date_cs2, end=end_date_cs2, freq='MS') 

# Re-grid the UBRIS/UIT CS-2 data to the IS-2 grid.
# Includes monthly resampling of the biweekly data
cs2_ubris = regrid_ubris_to_is2(mapProj, xIS2, yIS2, out_lons, out_lats, date_range_cs2,
                             dataPathCS2=current_directory+'/data/', dataset='uit_cryosat2_seaicethickness_nh_80km_v1p7.nc')

# Relabel the cs2_sea_ice_thickness_UBRIS variable to ice_thickness_cs2_ubris
cs2_ubris = cs2_ubris.rename({'cs2_sea_ice_thickness_UBRIS': 'ice_thickness_cs2_ubris'})


In [10]:
# Get the preliminary IS-2/CS-2 winter snow depths, downlaoded from Zenodo
cs2is2_snow_regridded_da = get_cs2is2_snow(mapProj, xIS2, yIS2, dataPathCS2=current_directory+'/data/uit_cs2-is2-ak_snow_depth_25km_v3.nc')

In [11]:
# Merge with other CS-2 data
cs2_ubris = cs2_ubris.merge({'cs2is2_snow_depth': cs2is2_snow_regridded_da})

In [12]:
# Merge all season IS-2 data and CS-2 datasets
IS2_CS2_allseason = IS2SITMOGR4_allseason.merge(cs2_ubris)

# Adjust all times to the middle (15th) of the month for plotting purposes
# (generally time defaults to the start of the month, with the MS function)
IS2_CS2_allseason['time'] = IS2_CS2_allseason['time'] + pd.Timedelta(days=14)

In [13]:
# Remove data outside of the period coincident with the SM-LG/IS-2 data
IS2_CS2_allseason = IS2_CS2_allseason.where(IS2_CS2_allseason['time'] <= pd.Timestamp('2021-07-20'), drop=True)
IS2_CS2_allseason = IS2_CS2_allseason.where(IS2_CS2_allseason['time'] >= pd.Timestamp('2018-11-01'), drop=True)
#IS2_CS2_allseason

In [14]:
# Only need the region mask for the first time step (missing from time=0 for some reason...)
IS2_CS2_allseason['region_mask'] = IS2_CS2_allseason['region_mask'].isel(time=1, drop=True)

In [15]:
# Save the dataset to netCDF file
output_path = './data/book_data_allseason.nc'
IS2_CS2_allseason.to_netcdf(output_path)

print(f"Dataset saved to {output_path}")

Dataset saved to ./data/book_data_allseason.nc


In [16]:
# Test loading the saved file
test_load = xr.open_dataset('./data/book_data_allseason.nc')
print("Successfully loaded saved dataset")

Successfully loaded saved dataset
